In [1]:
# Venkatramana Ramadev Krishnamurthy
# 202002265
# x2020cwk@stfx.ca

# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import pandas as pd  # data processing, CSV file I/O (e.g. pd.read_csv)
import pandas_profiling  # library for automatic EDA
from sklearn.ensemble import RandomForestClassifier
import re

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/titanic/train.csv
/kaggle/input/titanic/test.csv
/kaggle/input/titanic/gender_submission.csv


# **Reading Testing and Training Datasets**

In [2]:
train = pd.read_csv("/kaggle/input/titanic/train.csv")
print(train.keys())
train_data = train.drop(columns=['Survived'])
y_train = train['Survived']
print(train_data.head())

test = pd.read_csv("/kaggle/input/titanic/test.csv")
print(test.keys())
print(test.head())

Index(['PassengerId', 'Survived', 'Pclass', 'Name', 'Sex', 'Age', 'SibSp',
       'Parch', 'Ticket', 'Fare', 'Cabin', 'Embarked'],
      dtype='object')
   PassengerId  Pclass                                               Name  \
0            1       3                            Braund, Mr. Owen Harris   
1            2       1  Cumings, Mrs. John Bradley (Florence Briggs Th...   
2            3       3                             Heikkinen, Miss. Laina   
3            4       1       Futrelle, Mrs. Jacques Heath (Lily May Peel)   
4            5       3                           Allen, Mr. William Henry   

      Sex   Age  SibSp  Parch            Ticket     Fare Cabin Embarked  
0    male  22.0      1      0         A/5 21171   7.2500   NaN        S  
1  female  38.0      1      0          PC 17599  71.2833   C85        C  
2  female  26.0      0      0  STON/O2. 3101282   7.9250   NaN        S  
3  female  35.0      1      0            113803  53.1000  C123        S  
4    male  35.

# **Visualization for Analyzing Data**

In [3]:
report_train = pandas_profiling.ProfileReport(train_data)
display(report_train)
report_train.to_file(output_file='Training_Visualization.html')

report_test = pandas_profiling.ProfileReport(test)
display(report_test)
report_test.to_file(output_file='Testing_Visualization.html')

Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Summarize dataset:   0%|          | 0/24 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

# **Checking for Null Values**

In [4]:
print(train_data.isnull().sum())
print(test.isnull().sum())

PassengerId      0
Pclass           0
Name             0
Sex              0
Age            177
SibSp            0
Parch            0
Ticket           0
Fare             0
Cabin          687
Embarked         2
dtype: int64
PassengerId      0
Pclass           0
Name             0
Sex              0
Age             86
SibSp            0
Parch            0
Ticket           0
Fare             1
Cabin          327
Embarked         0
dtype: int64


# **Data Pre-processing**

In [5]:
# Grouping common titles
def title_preprocessing(title):
    if re.search("Mr", title) is not None:
        return 1
    elif re.search("Miss", title) is not None:
        return 2
    elif re.search("Mrs", title) is not None:
        return 3
    elif re.search("Ms", title) is not None:
        return 3
    elif re.search("Mme", title) is not None:
        return 3
    elif re.search("Mlle", title) is not None:
        return 2
    elif re.search("Capt", title) is not None:
        return 4
    elif re.search("Col", title) is not None:
        return 4
    elif re.search("Major", title) is not None:
        return 4
    elif re.search("Dr", title) is not None:
        return 4
    elif re.search("Rev", title) is not None:
        return 4
    elif re.search("Sir", title) is not None:
        return 5
    elif re.search("Don", title) is not None:
        return 5
    elif re.search("Dona", title) is not None:
        return 5
    elif re.search("Jonkheer", title) is not None:
        return 5
    elif re.search("the Countess", title) is not None:
        return 6
    elif re.search("Lady", title) is not None:
        return 6
    else:
        return 7

# Grouping commonly used titles
train_data['Name'] = train_data['Name'].map(title_preprocessing)
# Replacing Null values in Age with median value
train_data['Age'].fillna(train_data['Age'].median(), inplace=True)
# Replacing Null values in Embarked with 'S'
train_data['Embarked'].fillna(value='S', inplace=True)
# Replacing 'male' with 1 and 'female' with 0 for Sex column
train_data['Sex'] = train_data['Sex'].replace(['male', 'female'], [1, 0])
# Replacing 'S', 'Q', 'C' with 1, 2 and 3 respectively
train_data['Embarked'] = train_data['Embarked'].replace(['S', 'Q', 'C'], [1, 2, 3])
# Dropping columns which might not contribute much for the prediction
X_train = train_data.drop(columns=['PassengerId', 'Ticket', 'Cabin'])

# Grouping commonly used titles
test['Name'] = test['Name'].map(title_preprocessing)
# Replacing Null values in Age with median value
test['Age'].fillna(test['Age'].median(), inplace=True)
# Replacing Null values in Fare with median value
test['Fare'].fillna(test['Fare'].median(), inplace=True)
# Replacing 'male' with 1 and 'female' with 0 for Sex column
test['Sex'] = test['Sex'].replace(['male', 'female'], [1, 0])
# Replacing 'S', 'Q', 'C' with 1, 2 and 3 respectively
test['Embarked'] = test['Embarked'].replace(['S', 'Q', 'C'], [1, 2, 3])
# Dropping columns which might not contribute much for the prediction
X_test = test.drop(columns=['PassengerId', 'Ticket', 'Cabin'])

# **Supervised Machine Learning Algorithm**

In [6]:
# Implementing Random Forest Classifier
# Fitting the traininig data and training the classifier
RF = RandomForestClassifier()
RF.fit(X_train, y_train)
# Prediction on the test data
pred_rf = RF.predict(X_test)

# **Generating Submission File**

In [7]:
data = {'PassengerId': test['PassengerId'], 'Survived': pred_rf}
submission = pd.DataFrame(data)
submission.to_csv('submission.csv', index=False)